In [2]:
import sys
sys.path.append('../')
# from Data_Processing_Automation import Data_Visualization
from Data_Exploration.data_exploration_main import DataExploration
from Data_Cleansing.data_cleansing_main import DataCleansing
# import pandas as pd
# import plotly.express as px
# import plotly.graph_objects as go
# from scipy import stats
# import numpy as np

### Load Data

In [2]:
data_exp = DataExploration()
df = data_exp.load_data('../data/raw_data/Sasol_processed_data.csv', parse_dates=True, index_col=0)

In [3]:
target = 'OXO-5FI696 Augusta'

In [4]:
# using plotly to visualize the target column in df
fig = px.line(df, x=df.index, y=target, title='Target column')
fig.show()

### Z-Score

In [5]:
# use z-score to detect outliers and highlight them in the plot
z_scores = np.abs(stats.zscore(df[target]))
# print(z_scores)

threshold = 3
outliers = np.where(z_scores > threshold)
print(len(outliers[0]))
# print(outliers)

# highlight the outliers in the plot
fig = px.line(df, x=df.index, y=target, title='Target column')
fig.add_trace(go.Scatter(x=df.index[outliers], y=df[target].values[outliers], mode='markers', name='outliers'))
fig.show()

189


In [6]:
data_cleansing = DataCleansing(df)
data_cleansing.detect_outliers(col_name=target)

189 outliers detected
Lower bound: 4019.10
Upper bound: 16218.96


In [28]:
z_scores = np.abs(stats.zscore(df[target]))
# print(z_scores)

threshold = 2
outliers = np.where(z_scores > threshold)
# print(outliers)

# highlight the outliers in the plot
fig = px.line(df, x=df.index, y=target, title='Target column')
fig.add_trace(go.Scatter(x=df.index[outliers], y=df[target].values[outliers], mode='markers', name='outliers'))
fig.show()

### Moving Average

In [27]:
# use moving average to detect outliers and highlight them in the plot
# calculate moving average
df['moving_average'] = df[target].rolling(window=240).mean()
# print(df['moving_average'])

# calculate moving standard deviation
df['moving_std'] = df[target].rolling(window=240).std()
# print(df['moving_std'])

# calculate upper and lower bounds
df['upper_bound'] = df['moving_average'] + 5 * df['moving_std']
df['lower_bound'] = df['moving_average'] - 5 * df['moving_std']
# print(df['upper_bound'])
# print(df['lower_bound'])

# plot y, highlight the data points outside the upper and lower bounds
fig = px.line(df, x=df.index, y=target, title='Target column')
# fig.add_trace(go.Scatter(x=df.index, y=df['upper_bound'], mode='lines', name='upper bound'))
# fig.add_trace(go.Scatter(x=df.index, y=df['lower_bound'], mode='lines', name='lower bound'))

outliers = df[(df[target] > df['upper_bound']) | (df[target] < df['lower_bound'])]
fig.add_trace(go.Scatter(x=outliers.index, y=outliers[target], mode='markers', name='outliers'))
fig.show()